<h1><center> IT550: Information Retrieval<h1>
<h2> <center> Assignment 4: Document Retrieval and Evaluation (2) </h2>


<h4> <center> <b>Name : Arjun Vankani </h4>
<h4> <b> <center>ID : 202211036 </h4>

**Downloading Data set and Extracting**

In [16]:
!unzip  /content/drive/MyDrive/Person/gujarati_corpus.zip

Archive:  /content/drive/MyDrive/Person/gujarati_corpus.zip
replace gujarati_corpus/gu.docs.2011.tar? [y]es, [n]o, [A]ll, [N]one, [r]ename: Y
  inflating: gujarati_corpus/gu.docs.2011.tar  Y

  inflating: gujarati_corpus/gu.qrels.176-225.2012-v1.txt.gz  
replace gujarati_corpus/gu.topics.176-225.2012.txt? [y]es, [n]o, [A]ll, [N]one, [r]ename:   inflating: gujarati_corpus/gu.topics.176-225.2012.txt  


**There are Total 3 files in Fire-Dataset**

**1 Topic documnts , 2 Qrels and 3 TELEGRPAH folder zip in which we have lot of files**

In [3]:
!tar -xvf /content/gujarati_corpus/gu.docs.2011.tar

gu.docs.2011/
gu.docs.2011/gu_GujaratSamachar.tgz


**Extracting Folder files**

In [ ]:
!tar -xvzf /content/gu.docs.2011/gu_GujaratSamachar.tgz

In [5]:
!gunzip /content/gujarati_corpus/gu.qrels.176-225.2012-v1.txt.gz

**Downloding pytho terior**

In [ ]:
!pip install indic-nlp-library
!pip install python-terrier

**Importing filess**

In [9]:
import re
import gzip
import tarfile
import os
import gc
import pandas as pd

In [28]:
from indicnlp.tokenize import sentence_tokenize
from indicnlp.tokenize import indic_tokenize
from indicnlp.normalize.indic_normalize import IndicNormalizerFactory
import pyterrier as pt

**Initialize python terrier**


In [10]:
if not pt.started():
    pt.init()

terrier-assemblies 5.7 jar-with-dependencies not found, downloading to /root/.pyterrier...
Done
terrier-python-helper 0.0.7 jar not found, downloading to /root/.pyterrier...
Done


PyTerrier 0.9.2 has loaded Terrier 5.7 (built by craigm on 2022-11-10 18:30) and terrier-helper 0.0.7



**Extracting topic title content**

In [11]:
with open('/content/gujarati_corpus/gu.topics.176-225.2012.txt') as f:
    topics_file_content = f.read()

topics_file_content

'\ufeff<topics>\n\n<top lang=\'gu\'>\n<num>176</num>\n<title>વાય.એસ.આર. રેડ્ડી ની મૌત</title>\n<desc>આંધ્ર પ્રદેશ ના મુખ્ય મંત્રી વાય.એસ.આર. રેડ્ડી ની મૌત</desc>\n<narr>સંબંધિત દસ્તાવેજો એક હેલિકોપ્ટર અકસ્માત માં આંધ્ર પ્રદેશ મુખ્ય પ્રધાન વાય.એસ.આર. રેડ્ડી ની મૃત્યુ વિશે જાણકારી સમાવતા હોવા જોઈએ.</narr>\n</top>\n\n<top lang=\'gu\'>\n<num>177</num>\n<title>સંગીતકારો ભારત રત્ન</title>\n<desc>સંગીતકારો ને ભારત રત્ન એનાયત થવા વિશે માહિતી</desc>\n<narr>સંબંધિત દસ્તાવેજો માં પ્રખ્યાત સંગીતકારો પર (બંને ગાયકો અને વાધ્યવાદક જેમ કે રવિ શંકર, એમ.એસ. સુબ્બલક્ષ્મી અને લતા મંગેશકર જેવા) ભારત રત્ન એનાયત થવા સંબંધિત જાણકારી સમાવતા હોવા જોઈએ. આ સંગીતકારો વિશે લેખ (દા.ત. સંક્ષિપ્ત જીવનચરિત્ર, કોન્સર્ટના પ્રતિભાવો) ત્યાં સુધી માન્ય નથી જ્યાં સુધી તેમાં સંગીતકારને ભારત રત્ન એનાયત થયા નો (અથવા થશે તેનો) ખાસ ઉલ્લેખ ન થયો હોઈ.</narr>\n</top>\n\n<top lang=\'gu\'>\n<num>178</num>\n<title>એમ.જી.એન.આર.ઈ.જી.એ. યોજના</title>\n<desc>મહાત્મા ગાંધી રાષ્ટ્રીય ગ્રામીણ રોજગાર બાંહેધરી કાયદા હેઠળ મુખ્ય યોજનાઓ</desc>\n<n

**extracting all titles**

In [12]:
extracted_titles = []

with open('/content/gujarati_corpus/gu.topics.176-225.2012.txt', 'r', encoding='utf-8') as f:
    lines = f.readlines()
    inside_topic = False
    current_topic = ""

    for line in lines:
        if "<title>" in line:
            inside_topic = True
            current_topic = line.strip()
            current_topic += " " + line.strip()
            extracted_titles.append(current_topic)
            current_topic = ""

for title in extracted_titles:
    print(title)

<title>વાય.એસ.આર. રેડ્ડી ની મૌત</title> <title>વાય.એસ.આર. રેડ્ડી ની મૌત</title>
<title>સંગીતકારો ભારત રત્ન</title> <title>સંગીતકારો ભારત રત્ન</title>
<title>એમ.જી.એન.આર.ઈ.જી.એ. યોજના</title> <title>એમ.જી.એન.આર.ઈ.જી.એ. યોજના</title>
<title>ઑસ્ટ્રેલિયન એલચી કચેરી સામે બોમ્બમારો</title> <title>ઑસ્ટ્રેલિયન એલચી કચેરી સામે બોમ્બમારો</title>
<title>યુરો અપનાવાતા દેશો</title> <title>યુરો અપનાવાતા દેશો</title>
<title>પ્રથમ ક્રિકેટર જેણે 700 ટેસ્ટ વિકેટ લીધી</title> <title>પ્રથમ ક્રિકેટર જેણે 700 ટેસ્ટ વિકેટ લીધી</title>
<title>સ્ટીવ ઇરવીન ની મૃત્યુ</title> <title>સ્ટીવ ઇરવીન ની મૃત્યુ</title>
<title>ગુવાહાટી 2008 બોમ્બમારામાં નુકસાન</title> <title>ગુવાહાટી 2008 બોમ્બમારામાં નુકસાન</title>
<title>ચામુંડા મંદિર માં નાસભાગ</title> <title>ચામુંડા મંદિર માં નાસભાગ</title>
<title>આદર્શ હાઉસિંગ સોસાયટી કૌભાંડમાં રાજીનામું</title> <title>આદર્શ હાઉસિંગ સોસાયટી કૌભાંડમાં રાજીનામું</title>
<title>ઑસ્ટ્રેલિયામાં ભારતીય વિદ્યાર્થીઓ પર હુમલા</title> <title>ઑસ્ટ્રેલિયામાં ભારતીય વિદ્યાર્થીઓ પર હુમલા</title>


In [13]:
len(extracted_titles)

50

**extrcting using regex**

In [14]:
query_start_pattern = re.compile("<top lang='gu'>((.|\n)*?)</top>")
query_number_pattern = re.compile('<num>(.*)</num>')
query_title_pattern = re.compile('<title>(.*)</title>')
query_description_pattern = re.compile('<desc>((.|\n)*)</desc>')

queries_data = []
for query_match in re.finditer(query_start_pattern, topics_file_content):
    query_block = topics_file_content[query_match.start():query_match.end()]
    query_number = int(re.findall(query_number_pattern, query_block)[0])
    query_title = re.findall(query_title_pattern, query_block)
    query_desc = list(re.findall(query_description_pattern, query_block)[0])

    try:
        query_desc.remove('\n')
    except:
        pass
    query_desc = query_desc[0].strip()
    query_desc = query_desc.replace('\n', '')

    if query_title:
        queries_data.append([query_number, query_title[0], query_desc])

In [33]:
queries_data

[[176,
  'વાય.એસ.આર. રેડ્ડી ની મૌત',
  'આંધ્ર પ્રદેશ ના મુખ્ય મંત્રી વાય.એસ.આર. રેડ્ડી ની મૌત'],
 [177, 'સંગીતકારો ભારત રત્ન', 'સંગીતકારો ને ભારત રત્ન એનાયત થવા વિશે માહિતી'],
 [178,
  'એમ.જી.એન.આર.ઈ.જી.એ. યોજના',
  'મહાત્મા ગાંધી રાષ્ટ્રીય ગ્રામીણ રોજગાર બાંહેધરી કાયદા હેઠળ મુખ્ય યોજનાઓ'],
 [179,
  'ઑસ્ટ્રેલિયન એલચી કચેરી સામે બોમ્બમારો',
  'જકાર્તા માં ઑસ્ટ્રેલિયન એલચી કચેરી સામે બોમ્બમારો'],
 [180,
  'યુરો અપનાવાતા દેશો',
  'ચલણ તરીકે યુરો નો વિવિધ યુરોપીયન દેશો દ્વારા સ્વીકાર'],
 [181,
  'પ્રથમ ક્રિકેટર જેણે 700 ટેસ્ટ વિકેટ લીધી',
  'પ્રથમ ક્રિકેટર જેણે 700 ટેસ્ટ વિકેટ લીધી'],
 [182, 'સ્ટીવ ઇરવીન ની મૃત્યુ', 'મગર ના શિકારી સ્ટીવ ઇરવીન ની મૃત્યુ'],
 [183,
  'ગુવાહાટી 2008 બોમ્બમારામાં નુકસાન',
  '2008 માં ગુવાહાટી માં શ્રેણીબદ્ધ બોમ્બ વિસ્ફોટમાં મિલકતને નુકસાન'],
 [184,
  'ચામુંડા મંદિર માં નાસભાગ',
  'જોધપુર માં માતા ચામુંડા દેવી ના મંદિર ખાતે નાસભાગ માં જાનહાનિ'],
 [185,
  'આદર્શ હાઉસિંગ સોસાયટી કૌભાંડમાં રાજીનામું',
  'આદર્શ હાઉસિંગ સોસાયટી કૌભાંડના લીધે મુખ્ય પ્રધાને રાજીનામું આ

**Extracting  text from alldocument and make dataframes**

In [30]:
# Read and process relevance information for queries
with gzip.open('/content/gujarati_corpus/gu.qrels.176-225.2012-v1.txt.gz', 'r') as file:
    qrels_content = file.read().decode('utf-8')

lines_content = qrels_content.split('\n')

for i in range(len(lines_content)):
    lines_content[i] = lines_content[i].strip().split()

In [34]:
lines_content

[['176', 'Q0', 'gujarat_samachar_date_20031106_guj_supplement_23_leader', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20031106_guj_supplement_23_leader', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20031106_guj_supplement_23_leader', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20040512_guj_national_20_news5', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20040512_guj_national_20_news5', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20040512_guj_national_20_news5', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20040512_guj_national_9_news16', '1'],
 ['176', 'Q0', 'gujarat_samachar_date_20040512_guj_national_9_news16', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20040523_guj_national_5_news12', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20040523_guj_national_5_news12', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20040525_guj_national_21_Tuka', '0'],
 ['176', 'Q0', 'gujarat_samachar_date_20040525_guj_national_21_Tuka', '0'],
 ['176',
  'Q0',
  'gujarat_samachar_date_20040625_guj_supplement_23_

**Create a DataFrame**

In [18]:
query_relevance_df = pd.DataFrame(lines_content, columns=['qid', 'q0', 'docno', 'label'])
query_relevance_df = query_relevance_df.dropna()
query_relevance_df = query_relevance_df.astype({'label': 'int'})
query_relevance_df = query_relevance_df[['qid', 'docno', 'label']]

In [35]:
query_relevance_df


qid                                              docno  label
0     176  gujarat_samachar_date_20031106_guj_supplement_...      0
1     176  gujarat_samachar_date_20031106_guj_supplement_...      0
2     176  gujarat_samachar_date_20031106_guj_supplement_...      0
3     176  gujarat_samachar_date_20040512_guj_national_20...      0
4     176  gujarat_samachar_date_20040512_guj_national_20...      0
...   ...                                                ...    ...
3135  225  gujarat_samachar_date_20090822_guj_national_21...      0
3136  225  gujarat_samachar_date_20090829_guj_national_9_...      1
3137  225  gujarat_samachar_date_20090830_guj_supplement_...      1
3138  225  gujarat_samachar_date_20091008_guj_internation...      0
3139  225  gujarat_samachar_date_20091106_guj_gujarat_30_...      0

[3140 rows x 3 columns]

**Extract documents from tar files**

In [19]:
tar_file = tarfile.open('/content/gujarati_corpus/gu.docs.2011.tar')
tar_file.extractall('/content/gujarati_corpus/extracted_docs')
tar_file.close()

**Extract documents from nested tar files**

In [20]:
nested_tar_file = tarfile.open('/content/gujarati_corpus/extracted_docs/gu.docs.2011/gu_GujaratSamachar.tgz')
nested_tar_file.extractall('/content/gujarati_corpus/extracted_docs')
nested_tar_file.close()

**Exract data from one data file**

In [21]:
with open('/content/gujarati_corpus/extracted_docs/gu_GujaratSamachar/gsf2002/gujarat_samachar_date_20020101_guj_astro_1_dinmahima.txt') as f:
    document_content = f.read()

document_content

'<DOC>\n<DOCNO>gujarat_samachar_date_20020101_guj_astro_1_dinmahima</DOCNO>\n<TEXT>\nઆજે પહેલી જાન્યુઆરી, માગશર વદ  બીજ, ખ્રિસ્તી નૂતન વર્ષ ઈસવીસન ૨૦૦૨ આરંભ, શુભ કાર્ય માટે આજે સામાન્ય  દિવસ છે.\nખ્રિસ્તી  ભાઇબહેનોનું બેસતું વર્ષ :\nદુનિયામાં સૌથી વધુમાં વધુ  ફેલાએલા અને વધુમાં વધુ અનુયાયીઓ ધરાવતા ખ્રિસ્તી ધર્મના  સ્થાપક ઈસુ ખ્રિસ્ત સાથે સંકળાએલા ઈસવીસન ૨૦૦૨નો આજે આરંભ થાય છે.  ખ્રિસ્તી ભાઇબહેનો અને લગભગ આખી દુનિયા આજે નૂતન વર્ષ મનાવશે.\n૨૫મી ડિસેમ્બરના નાતાલ પર્વથી શરૂ કરીને  ૧ જાન્યુઆરી સુધી સૌ ખ્રિસ્તી ભાઇબહેનો આનંદ ઉલ્લાસનું પર્વ  મનાવે છે. ખ્રિસ્તી ધર્મના સામાન્ય સિધ્ધાંન્તો અનુસાર ભૂતકાળ,  ભવિષ્યકાળ અને વર્તમાનકાળ એ તો માનવસર્જિત સમયગણના છે. પરમ પ્રભુ ઈસુને  માટે તો સમય આવી રીતે વહેંચાએલો નથી પરંતુ અખંડ છે. સામાન્ય પરંપરા  પ્રમાણે જુદા જુદા દેશો પોતાના વર્ષની કાલગણના એટલે  કે નૂતન વર્ષનો પ્રારંભ જુદી જુદી રીતે કરે છે. પોતાના નવા  વરસને પોતાના દેશના કોઇ મહાન પુરુષ સાથે સાંકળે છે. જેમકે ભારતનું-  હિન્દુસ્તાનનું નવું વરસ મહાન આદર્શ રાજા વિક્રમ સાથે સંકળાએલ  છે અને આપણે વિક્રમ સંવત પ

In [31]:
document_text_pattern = re.compile('<TEXT>((.|\n)*)</TEXT>')
document_text = re.findall(document_text_pattern, document_content)[0][0].strip().replace('\n', '')
document_text

'આજે પહેલી જાન્યુઆરી, માગશર વદ  બીજ, ખ્રિસ્તી નૂતન વર્ષ ઈસવીસન ૨૦૦૨ આરંભ, શુભ કાર્ય માટે આજે સામાન્ય  દિવસ છે.ખ્રિસ્તી  ભાઇબહેનોનું બેસતું વર્ષ :દુનિયામાં સૌથી વધુમાં વધુ  ફેલાએલા અને વધુમાં વધુ અનુયાયીઓ ધરાવતા ખ્રિસ્તી ધર્મના  સ્થાપક ઈસુ ખ્રિસ્ત સાથે સંકળાએલા ઈસવીસન ૨૦૦૨નો આજે આરંભ થાય છે.  ખ્રિસ્તી ભાઇબહેનો અને લગભગ આખી દુનિયા આજે નૂતન વર્ષ મનાવશે.૨૫મી ડિસેમ્બરના નાતાલ પર્વથી શરૂ કરીને  ૧ જાન્યુઆરી સુધી સૌ ખ્રિસ્તી ભાઇબહેનો આનંદ ઉલ્લાસનું પર્વ  મનાવે છે. ખ્રિસ્તી ધર્મના સામાન્ય સિધ્ધાંન્તો અનુસાર ભૂતકાળ,  ભવિષ્યકાળ અને વર્તમાનકાળ એ તો માનવસર્જિત સમયગણના છે. પરમ પ્રભુ ઈસુને  માટે તો સમય આવી રીતે વહેંચાએલો નથી પરંતુ અખંડ છે. સામાન્ય પરંપરા  પ્રમાણે જુદા જુદા દેશો પોતાના વર્ષની કાલગણના એટલે  કે નૂતન વર્ષનો પ્રારંભ જુદી જુદી રીતે કરે છે. પોતાના નવા  વરસને પોતાના દેશના કોઇ મહાન પુરુષ સાથે સાંકળે છે. જેમકે ભારતનું-  હિન્દુસ્તાનનું નવું વરસ મહાન આદર્શ રાજા વિક્રમ સાથે સંકળાએલ  છે અને આપણે વિક્રમ સંવત પ્રારંભ- બેસતું વરસ એમ કહીએ છીએ. મુસલમાનોમાં  નવું વરસ હિજરી સંવત પ્રારંભ કહેવાય છે. તેમજ ત

**Create a list of document-text pairs**

In [ ]:
document_text_list = []
document_text_pattern = re.compile('<TEXT>((.|\n)*?)</TEXT>')
normalizer_factory = IndicNormalizerFactory()
text_normalizer = normalizer_factory.get_normalizer("gu")
count = 1

documents_folder = '/content/gujarati_corpus/extracted_docs/gu_GujaratSamachar'
for main_folder in os.listdir(documents_folder):
    year = main_folder[-4:]

    for doc_file in os.listdir(os.path.join(documents_folder, main_folder)):

        if count % 10000 == 0:
            print(count)
            gc.collect()
        count += 1
        doc_number = doc_file[:-4]

        with open(os.path.join(documents_folder, main_folder, doc_file)) as f:
            doc_text = f.read()
            text = re.findall(document_text_pattern, doc_text)[0][0].strip().replace('\n', '').replace("'", '')
            text = text_normalizer.normalize(text)
            text = indic_tokenize.trivial_tokenize(text, lang='gu')
            text = ' '.join([i for i in text if i not in '''!()-[]{};:'"\,<>./?@#$%^&*_~'''])

        document_text_list.append([doc_number, text])
        del text

In [36]:
document_text_list

[['gujarat_samachar_date_20020517_guj_busi_2_asps',
  'ગ્રીક ફિલસુફ પ્લેટોએ ધ રિપબ્લીક નામનાં ગ્રંથમાં લખેલું કે જ્યાં સુધી રાજા કે શાસક ફીલોસોફર પણ ન હોય અગર તો રાજા કે શાસકના ભાથામાં ફીલસુફીની તાકત અને રાજકીય મહાનતા તેમજ ડહાપણ ભરેલાં ન હોય ત્યાં સુધી નગરોના પ્રજાજનોને અવનવી આપત્તિા સતાવે છે માનવજાત જંપીને બેસી શકતી નથી જ્યારે રાજા કે શાસકમાં નૈતિકતા અને ફિલસૂફી હશે ત્યારે જ પ્રજાજનોને નિરાંતે જીવવા મળશે પ્લેટોનાં આ માપદંડથી આજના શાસકોને માપીએ તો જગતનાં તમામ શાસકો નાલાયક ઠરે છે મહારાષ્ટ્રનાં ઉપમુખ્યપ્રધાન છગન ભુજબળની કોમની જ હજારો યુવતીઓ કે યુવકો ૨૫ વર્ષની ઉંમરે પરણી શકતા નથી કારણ કે ગરીબ નવ યુગલને સુવા માટે ઝુંપડામાં જગા નથી પરણવા માટે વીંટી તો શું પણ કન્યા માટે સાડી લેવાનો વેંત નથી એ છગન ભુજબળનાં બેટાના લગ્નમાં લાખ્ખો રૂપિયા ખર્ચ થાય છે દસ હજાર લોકો જેમાંથી ૯૯ ટકા હ્ય્દયથી છગન ભુજબળને ધિક્કારતા હશે તે આ ૨૧મી સદીના યુગલને ભેટસોગાદ આપવા ઉમટતા હતા આ શું મોરલ પ્રોબ્લેમ છે હા આજ મોરલ પ્રોબ્લેમ છે મેન ફોર હિમસેલ્ફ નામનાં પુસ્તકમાં એરીક ફ્રોમ આજની નૈતિક સમસ્યાનો સ્ફોટ પાડે છે જે કૃષ્ણમૂર્ત

In [ ]:
document_df = pd.DataFrame(document_text_list, columns=['docno', 'text'])

pd_indexer = pt.DFIndexer("./pd_index", overwrite=True, tokeniser="UTFTokeniser")

index = pd_indexer.index(document_df["text"], document_df["docno"])


In [39]:
document_df

docno  \
0          gujarat_samachar_date_20020517_guj_busi_2_asps   
1       gujarat_samachar_date_20020325_guj_gujarat_62_...   
2       gujarat_samachar_date_20021101_guj_gujarat_9_n...   
3       gujarat_samachar_date_20021010_guj_gujarat_5_n...   
4           gujarat_samachar_date_20020807_guj_busi_1_ahd   
...                                                   ...   
313158  gujarat_samachar_date_20050519_guj_supplement_...   
313159   gujarat_samachar_date_20051207_guj_astro_2_index   
313160  gujarat_samachar_date_20050528_guj_supplement_...   
313161  gujarat_samachar_date_20050410_guj_gujarat_26_...   
313162  gujarat_samachar_date_20050522_guj_supplement_...   

                                                     text  
0       ગ્રીક ફિલસુફ પ્લેટોએ ધ રિપબ્લીક નામનાં ગ્રંથમા...  
1       પાટણ તા ૨૩પાટણ નગરપાલિકાનું વર્ષ ૨૦૦૨ ૦૩નું રૂ...  
2       વાહન ચોરીમેમનગર ગામમાં ચાની લારી પાસે પાર્ક કર...  
3       ગાંધીનગર બુધવારગુજરાત સરકારે એક જાહેરનામુ બહાર...  
4       એસીસી ૧૪૦ ૧૪૯ ૫૦ ૧૨૫ ૧૨૬જીટીએલ ૭૯ ૮૧ ૭૮ ૮૦ ૨૫લ...  
...                                                   ...  
313158  એકવાર એક જમીનદારનો પુત્ર સ્વામી રામતીર્થને મળવ...  
313159  સુપ્રભાતમ ધ્યેય જેટલું મહાન તેટલો જ માર્ગ લાંબ...  
313160  મધ્ય સાઈબરીયાના નિર્જન વિસ્તારમાં એક એકલા અટૂલ...  
313161  ગોપીપુરાના પોલીસકર્મીઓ ધમકી આપે છે કે બાંધકામ ...  
313162  વેકેશન આવે એટલે શ્રધ્ધાદેવીનું ઘર લાગણીતીર્થમા...  

[313163 rows x 2 columns]

**Index factory**

In [ ]:
index_factory = pt.IndexFactory.of(index)


In [37]:
index_factory

<org.terrier.structures.Index at 0x7ad9055d01d0 jclass=org/terrier/structures/Index jself=<LocalRef obj=0x579b94592810 at 0x7ad8e92910d0>>

**collection statistics**

In [38]:
collection_stats = index_factory.getCollectionStatistics().toString()
print(collection_stats)



Number of documents: 313163
Number of terms: 2691147
Number of postings: 83086577
Number of fields: 0
Number of tokens: 137158908
Field names: []
Positions:   false



**Inverted index to print postings**

In [40]:
pointer = index_factory.getLexicon()["document"]
for posting in index_factory.getInvertedIndex().getPostings(pointer):
    print(posting.toString() + " doclen=%d" % posting.getDocumentLength())


ID(70708) TF(1) doclen=217
ID(117147) TF(1) doclen=481
ID(148814) TF(1) doclen=144
ID(149507) TF(1) doclen=111
ID(150826) TF(1) doclen=118
ID(151172) TF(1) doclen=108
ID(151668) TF(1) doclen=91
ID(154307) TF(1) doclen=148
ID(154512) TF(1) doclen=102
ID(154888) TF(1) doclen=119
ID(155339) TF(1) doclen=85
ID(158992) TF(1) doclen=962
ID(161118) TF(1) doclen=163
ID(162052) TF(1) doclen=257
ID(162604) TF(1) doclen=105
ID(163394) TF(3) doclen=112
ID(163837) TF(2) doclen=82
ID(165808) TF(2) doclen=96
ID(167836) TF(1) doclen=75
ID(170338) TF(2) doclen=515
ID(170805) TF(3) doclen=109
ID(171897) TF(1) doclen=120
ID(173008) TF(1) doclen=90
ID(178615) TF(1) doclen=95
ID(181242) TF(1) doclen=80
ID(181703) TF(1) doclen=68
ID(182127) TF(1) doclen=108
ID(182207) TF(1) doclen=96
ID(182788) TF(1) doclen=116
ID(185250) TF(1) doclen=115
ID(186027) TF(1) doclen=175
ID(186264) TF(1) doclen=57
ID(187513) TF(1) doclen=94
ID(187848) TF(1) doclen=48
ID(187974) TF(1) doclen=77
ID(282714) TF(1) doclen=155
ID(2840

**TF-IDF weighting model**

In [41]:
tfidf_retriever = pt.BatchRetrieve(index_factory, wmodel="TF_IDF")
tfidf_retriever


BR(/content/pd_index/data.properties,{'terrierql': 'on', 'parsecontrols': 'on', 'parseql': 'on', 'applypipeline': 'on', 'localmatching': 'on', 'filters': 'on', 'decorate': 'on', 'wmodel': 'TF_IDF'},{'querying.processes': 'terrierql:TerrierQLParser,parsecontrols:TerrierQLToControls,parseql:TerrierQLToMatchingQueryTerms,matchopql:MatchingOpQLParser,applypipeline:ApplyTermPipeline,context_wmodel:org.terrier.python.WmodelFromContextProcess,localmatching:LocalManager$ApplyLocalMatching,qe:QueryExpansion,labels:org.terrier.learning.LabelDecorator,filters:LocalManager$PostFilterProcess,decorate:SimpleDecorateProcess', 'querying.postfilters': 'decorate:SimpleDecorate,site:SiteFilter,scope:Scope', 'querying.default.controls': 'wmodel:DPH,parsecontrols:on,parseql:on,applypipeline:on,terrierql:on,localmatching:on,filters:on,decorate:on', 'querying.allowed.controls': 'scope,qe,qemodel,start,end,site,scope,applypipeline', 'termpipelines': 'Stopwords,PorterStemmer'})

**Perform a search using the TF-IDF retriever**

In [47]:
search_query = "ગાંધીનગર "
search_results = tfidf_retriever.search(search_query)
print(search_results)

    qid   docid                                              docno  rank  \
0     1   97428  gujarat_samachar_date_20070804_guj_gujarat_57_...     0   
1     1  221297  gujarat_samachar_date_20080217_guj_gujarat_47_...     1   
2     1  257298  gujarat_samachar_date_20061101_guj_gujarat_7_n...     2   
3     1  289752  gujarat_samachar_date_20050325_guj_gujarat_10_...     3   
4     1  169908  gujarat_samachar_date_20040522_guj_gujarat_8_n...     4   
..   ..     ...                                                ...   ...   
995   1  285672  gujarat_samachar_date_20050223_guj_gujarat_7_n...   995   
996   1  132028  gujarat_samachar_date_20030522_guj_gujarat_18_...   996   
997   1  136250  gujarat_samachar_date_20030301_guj_gujarat_44_...   997   
998   1     964  gujarat_samachar_date_20020407_guj_gujarat_60_...   998   
999   1   16678  gujarat_samachar_date_20020214_guj_gujarat_36_...   999   

        score      query  
0    5.045355  ગાંધીનગર   
1    5.044468  ગાંધીનગર   
2    4

In [48]:
search_results


qid   docid                                              docno  rank  \
0     1   97428  gujarat_samachar_date_20070804_guj_gujarat_57_...     0   
1     1  221297  gujarat_samachar_date_20080217_guj_gujarat_47_...     1   
2     1  257298  gujarat_samachar_date_20061101_guj_gujarat_7_n...     2   
3     1  289752  gujarat_samachar_date_20050325_guj_gujarat_10_...     3   
4     1  169908  gujarat_samachar_date_20040522_guj_gujarat_8_n...     4   
..   ..     ...                                                ...   ...   
995   1  285672  gujarat_samachar_date_20050223_guj_gujarat_7_n...   995   
996   1  132028  gujarat_samachar_date_20030522_guj_gujarat_18_...   996   
997   1  136250  gujarat_samachar_date_20030301_guj_gujarat_44_...   997   
998   1     964  gujarat_samachar_date_20020407_guj_gujarat_60_...   998   
999   1   16678  gujarat_samachar_date_20020214_guj_gujarat_36_...   999   

        score      query  
0    5.045355  ગાંધીનગર   
1    5.044468  ગાંધીનગર   
2    4.989087  ગાંધીનગર   
3    4.945364  ગાંધીનગર   
4    4.929091  ગાંધીનગર   
..        ...        ...  
995  3.931317  ગાંધીનગર   
996  3.930314  ગાંધીનગર   
997  3.930314  ગાંધીનગર   
998  3.928332  ગાંધીનગર   
999  3.928332  ગાંધીનગર   

[1000 rows x 6 columns]

**Create a DataFrame from the list of query data**

In [49]:
query_data_df = pd.DataFrame(queries_data, columns=['qid', 'query', 'description'])

queries_df = query_data_df.iloc[:, :2]

transformed_queries = tfidf_retriever.transform(queries_df)


In [50]:
transformed_queries

qid   docid                                              docno  rank  \
0      176  276551   gujarat_samachar_date_20101202_vishesh_11_tantri     0   
1      176  271435  gujarat_samachar_date_20101208_purti_shatdal_2...     1   
2      176   41624  gujarat_samachar_date_20090904_guj_national_16...     2   
3      176   67717  gujarat_samachar_date_20091030_guj_national_13...     3   
4      176  256411  gujarat_samachar_date_20061107_guj_supplement_...     4   
...    ...     ...                                                ...   ...   
49995  225  104292  gujarat_samachar_date_20070509_guj_gujarat_32_...   995   
49996  225  145233  gujarat_samachar_date_20030206_guj_gujarat_25_...   996   
49997  225  221985  gujarat_samachar_date_20080503_guj_gujarat_33_...   997   
49998  225   56271  gujarat_samachar_date_20091101_guj_gujarat_16_...   998   
49999  225   70239  gujarat_samachar_date_20090213_guj_gujarat_7_n...   999   

          score                     query  
0      9.588750  વાય.એસ.આર. રેડ્ડી ની મૌત  
1      9.442517  વાય.એસ.આર. રેડ્ડી ની મૌત  
2      9.414364  વાય.એસ.આર. રેડ્ડી ની મૌત  
3      9.268043  વાય.એસ.આર. રેડ્ડી ની મૌત  
4      9.166071  વાય.એસ.આર. રેડ્ડી ની મૌત  
...         ...                       ...  
49995  4.011375      સેતાનિક વર્સેસ વિવાદ  
49996  4.011375      સેતાનિક વર્સેસ વિવાદ  
49997  4.011375      સેતાનિક વર્સેસ વિવાદ  
49998  4.008505      સેતાનિક વર્સેસ વિવાદ  
49999  4.008505      સેતાનિક વર્સેસ વિવાદ  

[50000 rows x 6 columns]

**Evaluate retrieval results using MAP, Precision@10, and BPREF metrics**

In [51]:
evaluation_metrics = ['map', 'P_10', 'bpref']
evaluation_results = pt.Utils.evaluate(transformed_queries, query_relevance_df, metrics=evaluation_metrics)


**Display the evaluation results**

In [52]:
print("Evaluation results:")
print(f"Mean Average Precision (MAP): {evaluation_results['map']}")
print(f"Precision@10: {evaluation_results['P_10']}")
print(f"BPREF: {evaluation_results['bpref']}")

Evaluation results:
Mean Average Precision (MAP): 0.24597185611738936
Precision@10: 0.23799999999999996
BPREF: 0.2556423058070736
